<a href="https://colab.research.google.com/github/khanakshah27/reccurent-ai/blob/main/recurrent.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
pip install tensorflow music21 numpy


In [ ]:
import numpy as np
melodies = [
    "C D E F G",
    "A B C D E",
    "G F E D C",
    "C E G C",
    "F A C F",
]

notes = " ".join(melodies).split()
unique = sorted(list(set(notes)))

note_to_int = {n:i for i,n in enumerate(unique)}
int_to_note = {i:n for n,i in note_to_int.items()}

seq = [note_to_int[n] for n in notes]




In [ ]:

X = []
y = []
seq_len = 5

for i in range(len(seq) - seq_len):
    X.append(seq[i:i+seq_len])
    y.append(seq[i+seq_len])

X = np.array(X)
y = np.array(y)

X = np.reshape(X, (X.shape[0], X.shape[1], 1))
X = X / float(len(unique))

In [ ]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout

model = Sequential([
    LSTM(128, return_sequences=True, input_shape=(X.shape[1], 1)),
    Dropout(0.2),

    LSTM(128),
    Dropout(0.2),

    Dense(len(unique), activation='softmax')
])

model.compile(loss='sparse_categorical_crossentropy', optimizer='adam')



/usr/local/lib/python3.12/dist-packages/keras/src/layers/rnn/rnn.py:199: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


In [ ]:
model.fit(X, y, epochs=50, batch_size=32)


Epoch 1/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step - loss: 1.9452
Epoch 2/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step - loss: 1.9358
Epoch 3/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step - loss: 1.9289
Epoch 4/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step - loss: 1.9214
Epoch 5/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step - loss: 1.9141
Epoch 6/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 148ms/step - loss: 1.9023
Epoch 7/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step - loss: 1.8881
Epoch 8/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step - loss: 1.8975
Epoch 9/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step - loss: 1.8750
Epoch 10/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step - loss: 1.8675
Epoch 11/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step - loss: 1.8536
Epoch 12/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step - loss: 1.8470
Epoch 13/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step - loss: 1.8362
Epoch 14/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step - loss: 1.8215
Epoch 15/50
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step - loss: 1.8427
Epoch 16/50
1/1 ━━━━━━━━━━━━━━━━━━━

In [ ]:
import random

pattern = list(X[np.random.randint(0, len(X))].flatten() * len(unique))

generated = []

for _ in range(50):
    x = np.array(pattern[-seq_len:]).reshape(1, seq_len, 1)
    x = x / float(len(unique))
    prediction = np.argmax(model.predict(x, verbose=0))

    generated.append(int_to_note[prediction])
    pattern.append(prediction)

print("Generated melody:")
print(" ".join(generated))


Generated melody:
C G F C C C C C E E E C C C C C E E E C C C C C E E E C C C C C E E E C C C C C E E E C C C C C E E


In [ ]:
from music21 import stream, note

melody_stream = stream.Stream()

for n in generated:
    melody_stream.append(note.Note(n))

melody_stream.write('midi', fp='generated_music.mid')


'generated_music.mid'

In [ ]:
from google.colab import files
files.download('generated_music.mid')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
!pip install midi2audio


In [ ]:
from midi2audio import FluidSynth

!apt-get update
!apt-get install -y fluidsynth

fs = FluidSynth()
fs.midi_to_audio('generated_music.mid', 'generated_music.wav')

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,632 B]
Hit:2 https://cli.github.com/packages stable InRelease
Get:3 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:6 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Hit:7 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Get:9 https://r2u.stat.illinois.edu/ubuntu jammy/main amd64 Packages [2,849 kB]
Get:10 http://security.ubuntu.com/ubuntu jammy-security/main amd64 Packages [3,623 kB]
Get:11 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [127 kB]
Get:12 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 Packages [1,598 kB]
Get:13 https://r2u.stat.illinois.edu/ubuntu jammy/main all Packages [9,537 kB]
Get:14 http://archive.ubunt

In [ ]:
from IPython.display import Audio
Audio('generated_music.wav')